In [1]:
# Cell 1: Import required libraries
import sys
from pathlib import Path
from IPython.display import Audio, display
import pretty_midi
from amt_backing_generator import AMTBackingGenerator

/Users/zhaluza/Desktop/coding/Audio Software/AMT Project/.venv/lib/python3.12/site-packages/pretty_midi/instrument.py:11: UserWarning: pkg_resources is deprecated as an API. See https://setuptools.pypa.io/en/latest/pkg_resources.html. The pkg_resources package is slated for removal as early as 2025-11-30. Refrain from using this package or pin to Setuptools<81.
  import pkg_resources
/Users/zhaluza/Desktop/coding/Audio Software/AMT Project/.venv/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
# Second cell - initialize and generate seed melody
# Initialize the generator
generator = AMTBackingGenerator(soundfont_path="soundfonts/soundfont.sf2")

Loading AMT model...
Model loaded on mps
Fluidsynth found: FluidSynth runtime version 2.4.6
Copyright (C) 2000-2025 Peter Hanappe and others.
Distributed under the LGPL license.
SoundFont(R) is a registered trademark of Creative Technology Ltd.

FluidSynth executable version 2.4.6
Sample type=double
Using soundfont: soundfonts/soundfont.sf2


## Seed Melody Details

The seed melody consists of four patterns spread across 8 bars:

1. **Bars 1-2**: Fast ascending arpeggio with octave jumps (32nd notes)
2. **Bars 3-4**: Rapid descending sequence with syncopation (mix of 16th and 32nd notes)
3. **Bars 5-6**: Fast alternating pattern with held notes (32nd notes with some held notes)
4. **Bars 7-8**: Rapid scale runs with octave jumps (32nd notes)

The melody is in C major and uses a bright sawtooth synth sound (Lead 2).

In [5]:
TEMPO = 240

In [6]:
# Create and preview the seed melody
print("Generating seed melody...")
seed_midi = generator.create_seed_melody(tempo=TEMPO)

# Save and preview the seed melody
print("\nPreviewing seed melody:")
seed_audio = generator.save_and_preview(seed_midi, "seed_melody.mid")
display(seed_audio)

Generating seed melody...
[DEBUG] Seed: tempo=240, beats_per_bar=4, seconds_per_bar=1.0
[DEBUG] Seed: Note pitch=72, start=0, end=0.25
[DEBUG] Seed: Note pitch=79, start=0.25, end=0.375
[DEBUG] Seed: Note pitch=76, start=0.375, end=0.5
[DEBUG] Seed melody: actual MIDI tempos: [240.]

Previewing seed melody:
Saved to output/seed_melody.mid
Running command: fluidsynth -F /var/folders/vc/hw7nmbfd7dj1h43rbxq6gkmw0000gn/T/tmpmiy8sxjx.wav -r 44100 -g 1.0 -i /var/folders/vc/hw7nmbfd7dj1h43rbxq6gkmw0000gn/T/tmpkrx5ujr0.mid soundfonts/soundfont.sf2 -q
Saved audio to output/seed_melody.wav
Running command: fluidsynth -F /var/folders/vc/hw7nmbfd7dj1h43rbxq6gkmw0000gn/T/tmptvedxvy5.wav -r 44100 -g 1.0 -i /var/folders/vc/hw7nmbfd7dj1h43rbxq6gkmw0000gn/T/tmph7gedewt.mid soundfonts/soundfont.sf2 -q


In [7]:
print("Generating backing track...")
backing_track = generator.create_backing_track(tempo=TEMPO)
print("Backing track generated. Preview:")
backing_audio = generator.preview_audio(backing_track)
display(backing_audio)

Generating backing track...
[DEBUG] Backing: tempo=240, beats_per_bar=4, seconds_per_bar=1.0
[DEBUG] Backing: Note pitch=60, start=0.0, end=1.0
[DEBUG] Backing: Note pitch=64, start=0.0, end=1.0
[DEBUG] Backing: Note pitch=67, start=0.0, end=1.0
[DEBUG] Backing track: actual MIDI tempos: [240.]
Backing track generated. Preview:
Running command: fluidsynth -F /var/folders/vc/hw7nmbfd7dj1h43rbxq6gkmw0000gn/T/tmp7_806tze.wav -r 44100 -g 1.0 -i /var/folders/vc/hw7nmbfd7dj1h43rbxq6gkmw0000gn/T/tmp2e1dfc8h.mid soundfonts/soundfont.sf2 -q


In [8]:
print("\nGenerating lead melody...")
lead_melody = generator.generate_lead_melody(backing_track)
if lead_melody:
    print("Lead melody generated. Preview:")
    lead_audio = generator.preview_audio(lead_melody)
    display(lead_audio)
    
    # Create and preview combined track
    print("\nCombined track preview:")
    combined = pretty_midi.PrettyMIDI()
    for instrument in backing_track.instruments:
        combined.instruments.append(instrument)
    for instrument in lead_melody.instruments:
        combined.instruments.append(instrument)
    
    combined_audio = generator.preview_audio(combined)
    display(combined_audio)
    
    # Save all tracks
    print("\nSaving tracks to output directory...")
    generator.save_and_preview(backing_track, "backing_track.mid")
    generator.save_and_preview(lead_melody, "lead_melody.mid")
    generator.save_and_preview(combined, "combined_track.mid")
    print("All tracks saved to output directory!")
else:
    print("Failed to generate lead melody")


Generating lead melody...
Converting backing track to events...
[DEBUG] Seed: tempo=120, beats_per_bar=4, seconds_per_bar=2.0
[DEBUG] Seed: Note pitch=72, start=0, end=0.5
[DEBUG] Seed: Note pitch=79, start=0.5, end=0.75
[DEBUG] Seed: Note pitch=76, start=0.75, end=1.0
[DEBUG] Seed melody: actual MIDI tempos: [120.]
Saved seed melody to output/seed_melody.mid
Generating lead melody with 985 conditioning events...
Generation failed: name 'seconds_per_bar' is not defined
Failed to generate lead melody


In [ ]:
# Optional - Generate with different parameters
# You can modify these parameters to experiment
tempo = 130  # Try different tempos
duration = 16  # Try different durations

print(f"\nGenerating new track with tempo={tempo}, duration={duration}...")
new_backing = generator.create_backing_track(tempo=tempo, duration_seconds=duration)
new_lead = generator.generate_lead_melody(new_backing, duration_seconds=duration)

if new_lead:
    print("New track generated. Preview:")
    new_combined = pretty_midi.PrettyMIDI()
    for instrument in new_backing.instruments:
        new_combined.instruments.append(instrument)
    for instrument in new_lead.instruments:
        new_combined.instruments.append(instrument)
    
    new_audio = generator.preview_audio(new_combined)
    display(new_audio)
    
    # Save the new track
    generator.save_and_preview(new_combined, "new_track.mid")
    print("New track saved to output/new_track.mid")